# A full business solution

Let's assume I publish a weekly oline newletter every week where I talk about one organization and one famous personality. 

I am going to create a program to quickly summarize information about an organization or a person and publish my newsletter.

Just to be fancy, I will also show you how we can publish in a streaming fashion in this notebook! But you'll have to run this notebook for the streaming experience. :) 

In [1]:
import os
import requests
import json
from typing import List
from dotenv import load_dotenv
from bs4 import BeautifulSoup
from IPython.display import Markdown, display, update_display
from openai import OpenAI

In [27]:
#This week in my newsletter I am showcasing summarizing OpenAI and MerylStreep!
open_ai_wiki_url = "https://en.wikipedia.org/wiki/OpenAI"
meryl_wiki_url = "https://en.wikipedia.org/wiki/Meryl_Streep"

In [2]:
# Initialize and constants

load_dotenv(override=True)
api_key = os.getenv('OPENAI_API_KEY')

if api_key and api_key.startswith('sk-proj-') and len(api_key)>10:
    print("API key looks good so far")
else:
    print("There might be a problem with your API key? Please visit the troubleshooting notebook!")
    
MODEL = 'gpt-4o-mini'
openai = OpenAI()

API key looks good so far


In [3]:
# A class to represent a Webpage

# Some websites need you to use proper headers when fetching them:
headers = {
 "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/117.0.0.0 Safari/537.36"
}

class Website:
    """
    A utility class to represent a Website that we have scraped, now with links
    """

    def __init__(self, url):
        self.url = url
        response = requests.get(url, headers=headers)
        self.body = response.content
        soup = BeautifulSoup(self.body, 'html.parser')
        self.title = soup.title.string if soup.title else "No title found"
        if soup.body:
            for irrelevant in soup.body(["script", "style", "img", "input"]):
                irrelevant.decompose()
            self.text = soup.body.get_text(separator="\n", strip=True)
        else:
            self.text = ""
        links = [link.get('href') for link in soup.find_all('a')]
        self.links = [link for link in links if link]

    def get_contents(self):
        return f"Webpage Title:\n{self.title}\nWebpage Contents:\n{self.text}\n\n"

In [17]:
wiki_openai = Website(open_ai_wiki_url)
wiki_openai.links

['#bodyContent',
 '/wiki/Main_Page',
 '/wiki/Wikipedia:Contents',
 '/wiki/Portal:Current_events',
 '/wiki/Special:Random',
 '/wiki/Wikipedia:About',
 '//en.wikipedia.org/wiki/Wikipedia:Contact_us',
 '/wiki/Help:Contents',
 '/wiki/Help:Introduction',
 '/wiki/Wikipedia:Community_portal',
 '/wiki/Special:RecentChanges',
 '/wiki/Wikipedia:File_upload_wizard',
 '/wiki/Special:SpecialPages',
 '/wiki/Main_Page',
 '/wiki/Special:Search',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=OpenAI',
 '/w/index.php?title=Special:UserLogin&returnto=OpenAI',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=OpenAI',
 '/w/index.php?title=Special:UserLogin&returnto=OpenAI',
 '/wiki/Help:Introduction',
 '/wiki/Special:MyContributions',
 '/wiki/Special:MyTalk',
 '#',
 '#History',


In [19]:
wiki_meryl = Website(meryl_wiki_url)
wiki_meryl.links

['#bodyContent',
 '/wiki/Main_Page',
 '/wiki/Wikipedia:Contents',
 '/wiki/Portal:Current_events',
 '/wiki/Special:Random',
 '/wiki/Wikipedia:About',
 '//en.wikipedia.org/wiki/Wikipedia:Contact_us',
 '/wiki/Help:Contents',
 '/wiki/Help:Introduction',
 '/wiki/Wikipedia:Community_portal',
 '/wiki/Special:RecentChanges',
 '/wiki/Wikipedia:File_upload_wizard',
 '/wiki/Special:SpecialPages',
 '/wiki/Main_Page',
 '/wiki/Special:Search',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep',
 '/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep',
 'https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en',
 '/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep',
 '/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep',
 '/wiki/Help:Introduction',
 '/wiki/Special:MyContributions',
 '/wiki/Special:MyTa

## First step: Have GPT-4o-mini figure out which links are relevant

### Use a call to gpt-4o-mini to read the links on a webpage, and respond in structured JSON.  
It should decide which links are relevant, and replace relative links such as "/about" with "https://company.com/about".  
We will use "one shot prompting" in which we provide an example of how it should respond in the prompt.

This is an excellent use case for an LLM, because it requires nuanced understanding. Imagine trying to code this without LLMs by parsing and analyzing the webpage - it would be very hard!

Sidenote: there is a more advanced technique called "Structured Outputs" in which we require the model to respond according to a spec. We cover this technique in Week 8 during our autonomous Agentic AI project.

In [49]:
link_system_prompt = "You are provided with a list of links found on a wikipedia search result page. \
You are able to decide which of the links would be most relevant to include in a creative snapshot summary about the topic searched on wikipedia., \
such as links technical terms, important people listed in the wikipedia description, links to any historical references, books, movies, awards, etc,.\n"
link_system_prompt += "You should respond in JSON as in these examples:"
link_system_prompt += """
{
    "links": [
        {"type": f"{cat['type']} - {item['name']}", "url": item["url"]}
        for cat in original_data["links"]
        for item in cat.get("people", []) + cat.get("items", [])
    ]
}
"""
link_system_prompt += """
{
    "links": [
        {"type": "University: Vassar College (AB)", "url": "https://full.url/goes/here/uni1"},
        {"type": "University: Yale University (MFA)", "url": "https://full.url/goes/here/uni2"},
        {"type": "Spouse - Don Gummer", "url": "https://another.full.url/person1"},
        {"type": "Partner - John Cazale", "url": "https://another.full.url/person2"},
        {"type": "Child: Henry", "url": "https://another.full.url/child1"},
        {"type": "Child: Mamie", "url": "https://another.full.url/child2"},
        {"type": "Child: Grace", "url": "https://another.full.url/child3"},
        {"type": "Child: Louisa", "url": "https://another.full.url/child4"},
        {"type": "film", "url": "https://another.full.url/child1"},
        {"type": "film", "url": "https://another.full.url/child1"},
        {"type": "Award: BAFTA", "url": "https://another.full.url/award1"},
        {"type": "Award: Tony", "url": "https://another.full.url/award2"},
        {"type": "Award: Emmy", "url": "https://another.full.url/award3"}
    ]
}
"""

In [50]:
print(link_system_prompt)

You are provided with a list of links found on a wikipedia search result page. You are able to decide which of the links would be most relevant to include in a creative snapshot summary about the topic searched on wikipedia., such as links technical terms, important people listed in the wikipedia description, links to any historical references, books, movies, awards, etc,.
You should respond in JSON as in these examples:
{
    "links": [
        {"type": f"{cat['type']} - {item['name']}", "url": item["url"]}
        for cat in original_data["links"]
        for item in cat.get("people", []) + cat.get("items", [])
    ]
}

{
    "links": [
        {"type": "University: Vassar College (AB)", "url": "https://full.url/goes/here/uni1"},
        {"type": "University: Yale University (MFA)", "url": "https://full.url/goes/here/uni2"},
        {"type": "Spouse - Don Gummer", "url": "https://another.full.url/person1"},
        {"type": "Partner - John Cazale", "url": "https://another.full.url/pe

In [51]:
def get_links_user_prompt(website):
    user_prompt = f"Here is the list of links on the website of {website.url} - "
    user_prompt += "please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. \
Do not include Terms of Service, Privacy, email links.\n"
    user_prompt += "Links (some might be relative links):\n"
    user_prompt += "\n".join(website.links)
    return user_prompt

In [52]:
print(get_links_user_prompt(wiki_openai))

Here is the list of links on the website of https://en.wikipedia.org/wiki/OpenAI - please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. Do not include Terms of Service, Privacy, email links.
Links (some might be relative links):
#bodyContent
/wiki/Main_Page
/wiki/Wikipedia:Contents
/wiki/Portal:Current_events
/wiki/Special:Random
/wiki/Wikipedia:About
//en.wikipedia.org/wiki/Wikipedia:Contact_us
/wiki/Help:Contents
/wiki/Help:Introduction
/wiki/Wikipedia:Community_portal
/wiki/Special:RecentChanges
/wiki/Wikipedia:File_upload_wizard
/wiki/Special:SpecialPages
/wiki/Main_Page
/wiki/Special:Search
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en
/w/index.php?title=Special:CreateAccount&returnto=OpenAI
/w/index.php?title=Special:UserLogin&returnto=OpenAI
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&u

In [53]:
print(get_links_user_prompt(wiki_meryl))

Here is the list of links on the website of https://en.wikipedia.org/wiki/Meryl_Streep - please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. Do not include Terms of Service, Privacy, email links.
Links (some might be relative links):
#bodyContent
/wiki/Main_Page
/wiki/Wikipedia:Contents
/wiki/Portal:Current_events
/wiki/Special:Random
/wiki/Wikipedia:About
//en.wikipedia.org/wiki/Wikipedia:Contact_us
/wiki/Help:Contents
/wiki/Help:Introduction
/wiki/Wikipedia:Community_portal
/wiki/Special:RecentChanges
/wiki/Wikipedia:File_upload_wizard
/wiki/Special:SpecialPages
/wiki/Main_Page
/wiki/Special:Search
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=en.wikipedia.org&uselang=en
/w/index.php?title=Special:CreateAccount&returnto=Meryl+Streep
/w/index.php?title=Special:UserLogin&returnto=Meryl+Streep
https://donate.wikimedia.org/?wmf_source=donate&wmf_medium=sidebar&wmf_campaign=

In [54]:
def get_links(url):
    website = Website(url)
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": link_system_prompt},
            {"role": "user", "content": get_links_user_prompt(website)}
      ],
        response_format={"type": "json_object"}
    )
    result = response.choices[0].message.content
    return json.loads(result)

In [55]:
get_links(open_ai_wiki_url)

{'links': [{'type': 'Official Website', 'url': 'https://openai.com/'},
  {'type': 'Key Person: Sam Altman',
   'url': 'https://en.wikipedia.org/wiki/Sam_Altman'},
  {'type': 'Key Person: Elon Musk',
   'url': 'https://en.wikipedia.org/wiki/Elon_Musk'},
  {'type': 'Key Person: Ilya Sutskever',
   'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'},
  {'type': 'Key Person: Greg Brockman',
   'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'},
  {'type': 'Key Person: Sarah Friar',
   'url': 'https://en.wikipedia.org/wiki/Sarah_Friar'},
  {'type': 'Product: ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'},
  {'type': 'Product: DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'},
  {'type': 'Product: OpenAI Codex',
   'url': 'https://en.wikipedia.org/wiki/OpenAI_Codex'},
  {'type': 'Product: GPT-5', 'url': 'https://en.wikipedia.org/wiki/GPT-5'},
  {'type': 'Research Area: Artificial Intelligence',
   'url': 'https://en.wikipedia.org/wiki/Artificial_intelligence'},
  {'typ

In [56]:
get_links(meryl_wiki_url)

{'links': [{'type': 'University: Vassar College',
   'url': 'https://en.wikipedia.org/wiki/Vassar_College'},
  {'type': 'University: Yale University',
   'url': 'https://en.wikipedia.org/wiki/Yale_University'},
  {'type': 'Spouse: Don Gummer',
   'url': 'https://en.wikipedia.org/wiki/Don_Gummer'},
  {'type': 'Partner: John Cazale',
   'url': 'https://en.wikipedia.org/wiki/John_Cazale'},
  {'type': 'Child: Henry Wolfe',
   'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'},
  {'type': 'Child: Mamie Gummer',
   'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'},
  {'type': 'Child: Grace Gummer',
   'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'},
  {'type': 'Child: Louisa Jacobson',
   'url': 'https://en.wikipedia.org/wiki/Louisa_Jacobson'},
  {'type': 'Film: The Iron Lady',
   'url': 'https://en.wikipedia.org/wiki/The_Iron_Lady_(film)'},
  {'type': 'Film: Kramer vs. Kramer',
   'url': 'https://en.wikipedia.org/wiki/Kramer_vs._Kramer'},
  {'type': 'Film: Julie & Julia',
   'url':

## Second step: make a summary page for my newsletter!

Assemble all the details into another prompt to GPT4-o, and also get information about the important aspects with in the organization or persona's wiki.

In [57]:
def get_all_details(url):
    result = "Landing page:\n"
    result += Website(url).get_contents()
    links = get_links(url)
    print("Found links:", links)
    for link in links["links"]:
        result += f"\n\n{link['type']}\n"
        result += Website(link["url"]).get_contents()
    return result

In [58]:
print(get_all_details(open_ai_wiki_url))

Found links: {'links': [{'type': 'Official Website', 'url': 'https://openai.com/'}, {'type': 'Founder: Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Co-founder: Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Co-founder: Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Co-founder: Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Co-founder: John Schulman', 'url': 'https://en.wikipedia.org/wiki/John_Schulman'}, {'type': 'GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'GPT-4', 'url': 'https://en.wikipedia.org/wiki/GPT-4'}, {'type': 'DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'OpenAI Codex', 'url': 'https://en.wikipedia.org/wiki/OpenAI_Codex'}, {'type': 'ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'OpenAI Five', 'url': 'https://en.wikipedia.org/wiki/OpenAI_Five'}, {'type': 'Whisper (speech recognition system

In [59]:
print(get_all_details(meryl_wiki_url))

Found links: {'links': [{'type': 'University: Vassar College', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'University: Yale University (MFA)', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Spouse - Don Gummer', 'url': 'https://en.wikipedia.org/wiki/Don_Gummer'}, {'type': 'Partner - John Cazale', 'url': 'https://en.wikipedia.org/wiki/John_Cazale'}, {'type': 'Child: Henry Wolfe', 'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'}, {'type': 'Child: Mamie Gummer', 'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'}, {'type': 'Child: Grace Gummer', 'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'}, {'type': 'Child: Louisa Jacobson', 'url': 'https://en.wikipedia.org/wiki/Louisa_Jacobson'}, {'type': 'film - Julie & Julia', 'url': 'https://en.wikipedia.org/wiki/Julie_%26_Julia'}, {'type': 'film - The Devil Wears Prada', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'film - The Iron Lady', 'url': 'https://en.wikipe

In [60]:
system_prompt = "You are the editor of a graduate student newsletter in a business school. Every week you write a piece on an organization and a famous persona \
in which you borrow and summarize contents from their wiki page. In fact you call your piece \"What does Wiki say!\".  In addition to summarizing their wikipedia page \
you also highlight relevance facts that relate to this org or person from the the contents of several relevant pages linked on the org or persona\'s page. \
and creates a short brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
For an organization include details of founders, competitors, major products, funding or stock outlook, and future directions. For a person include their work, what made them \
who they are, import works, awards and recognitions, important life events both professions and personal, and info about important people in their lives. Oh an btw, \
you have a great sense of humor but that you whip out 15-20% of the times for maximum impact in your writing.  Respond in markdown."

In [81]:
def get_brochure_user_prompt(name, url):
    user_prompt = f"You are looking at the wikiepdia of a company or person called: {name}\n"
    user_prompt += f"Here are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\n"
    user_prompt += get_all_details(url)
    user_prompt = user_prompt[:5_000] # Truncate if more than 5,000 characters
    return user_prompt

In [82]:
get_brochure_user_prompt("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'OpenAI Official Website', 'url': 'https://openai.com/'}, {'type': 'Founding - OpenAI', 'url': 'https://en.wikipedia.org/wiki/OpenAI#History'}, {'type': 'Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'OpenAI Codex', 'url': 'https://en.wikipedia.org/wiki/OpenAI_Codex'}, {'type': 'OpenAI Five', 'url': 'https://en.wikipedia.org/wiki/OpenAI_Five'}, {'type': "OpenAI's Partnership with Microsoft", 'url': 'https://www.theverge.com/2019/7/22/20703578/microsoft-openai-investment-partnership-1-billion-azur

'You are looking at the wikiepdia of a company or person called: OpenAI\nHere are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\nLanding page:\nWebpage Title:\nOpenAI - Wikipedia\nWebpage Contents:\nJump to content\nMain menu\nMain menu\nmove to sidebar\nhide\nNavigation\nMain page\nContents\nCurrent events\nRandom article\nAbout Wikipedia\nContact us\nContribute\nHelp\nLearn to edit\nCommunity portal\nRecent changes\nUpload file\nSpecial pages\nSearch\nSearch\nAppearance\nDonate\nCreate account\nLog in\nPersonal tools\nDonate\nCreate account\nLog in\nPages for logged out editors\nlearn more\nContributions\nTalk\nContents\nmove to sidebar\nhide\n(Top)\n1\nHistory\nToggle History subsection\n1.1\n2015: founding and initial motivations\n1.2\n2016–2018: Non-profit beginnings\n1.3\n2019: Transition from non-profit\n1.4\n2020–2023: ChatGPT, DALL-E, partnership with Microsoft\n1.5\n2024: Public/Non-

In [83]:
get_brochure_user_prompt("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'University: Vassar College', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'University: Yale University (MFA)', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Spouse: Don Gummer', 'url': 'https://en.wikipedia.org/wiki/Don_Gummer'}, {'type': 'Parent: Mary Wilkinson Streep', 'url': 'https://en.wikipedia.org/wiki/Mary_Wilkinson_Streep'}, {'type': 'Child: Henry Wolfe', 'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'}, {'type': 'Child: Mamie Gummer', 'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'}, {'type': 'Child: Grace Gummer', 'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'}, {'type': 'Film: Julia (1977)', 'url': 'https://en.wikipedia.org/wiki/Julia_(1977_film)'}, {'type': 'Film: Kramer vs. Kramer', 'url': 'https://en.wikipedia.org/wiki/Kramer_vs._Kramer'}, {'type': 'Film: Sophie’s Choice', 'url': 'https://en.wikipedia.org/wiki/Sophie%27s_Choice_(film)'}, {'type': 'Film: The Iron Lady', 'url': 'https://e

'You are looking at the wikiepdia of a company or person called: Meryl\nHere are the contents of its their wiki page and other relevant pages; use this information to write a short newsletter article on them in markdown.\nLanding page:\nWebpage Title:\nMeryl Streep - Wikipedia\nWebpage Contents:\nJump to content\nMain menu\nMain menu\nmove to sidebar\nhide\nNavigation\nMain page\nContents\nCurrent events\nRandom article\nAbout Wikipedia\nContact us\nContribute\nHelp\nLearn to edit\nCommunity portal\nRecent changes\nUpload file\nSpecial pages\nSearch\nSearch\nAppearance\nDonate\nCreate account\nLog in\nPersonal tools\nDonate\nCreate account\nLog in\nPages for logged out editors\nlearn more\nContributions\nTalk\nContents\nmove to sidebar\nhide\n(Top)\n1\nEarly life and education\n2\nCareer\nToggle Career subsection\n2.1\n1970s: Early work and breakthrough\n2.2\n1980s: Rise to prominence\n2.3\n1990s: Commercial fluctuations\n2.4\n2000s: Career resurgence and stage work\n2.5\n2010s: Furthe

In [84]:
def create_brochure(name, url):
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
    )
    result = response.choices[0].message.content
    display(Markdown(result))

In [85]:
create_brochure("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'Official Website', 'url': 'https://openai.com/'}, {'type': 'Key Person: Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Key Person: Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Key Person: Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Key Person: Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Key Person: Mira Murati', 'url': 'https://en.wikipedia.org/wiki/Mira_Murati'}, {'type': 'Key Person: Sarah Friar', 'url': 'https://en.wikipedia.org/wiki/Sarah_Friar'}, {'type': 'Products: ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Products: DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Products: GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'Products: GPT-4', 'url': 'https://en.wikipedia.org/wiki/GPT-4'}, {'type': 'Company Background: OpenAI Five', 'url': 'https://en.wikipedia

```markdown
# What does Wiki say! - OpenAI

**This week, let's dive into the world of OpenAI, the megastar of artificial intelligence!** 🎉

### A Brief History
Founded on **December 8, 2015**, by a star-studded cast including **Sam Altman**, **Elon Musk**, and **Greg Brockman**, OpenAI began with the bright idea of developing safe and beneficial artificial general intelligence (AGI). Who knew a simple founding meeting in San Francisco could lead to such a monumental venture? 

Initially a non-profit, they transitioned to a "capped-profit" model in 2019 to attract investment. Think of them as a charitable organization with a bottom line—after all, money doesn't grow on trees! 🌳💸 

### Milestones
From launching **GPT-1** to beautifully generating images with **DALL-E** and helping coders via **OpenAI Codex**, they've set the AI world ablaze. As of 2024, OpenAI is expected to reach a revenue of **$3.7 billion**—not too shabby for a company with a net income of approximately **-$5 billion**. It’s like opening a lemonade stand and selling millions, but forgetting to buy lemons. 🍋 

### Key People
- **Sam Altman**: The charismatic CEO who probably doesn’t sleep at all. 
- **Greg Brockman**: President and the “man behind the scenes” making sure everything runs smoothly.
- **Bret Taylor**: Chairman, probably holding meetings while surfing. Just kidding—he’s all business!

### Products Galore
OpenAI serves the world a buffet of innovations:
- **GPT-4**: Chatting and writing like your favorite English professor.
- **DALL-E**: Making Picasso blush with your own generated art.
- **ChatGPT**: Your 3 AM therapist that's always available. (Hope it can help with your existential crises, though!)

### Competitors
Let’s not forget those pesky competitors! They include:
- **Google DeepMind**: The brainy kid who likes to be the teacher's pet.
- **Anthropic**: OpenAI but with a twist of philosophy—that's right, they're aiming for ethical AI!

### Future Directions
As they move forward, OpenAI has plans for partnerships (yes, there is such a thing as AI matchmaking!), including exciting collaborations with **Microsoft** and **Apple**. We can only imagine what they could concoct—perhaps an AI-powered smart fridge that advises on healthy eating? 🍏🥗

**In Summary:** OpenAI is a dynamic, somewhat chaotic mixture of technological brilliance, ethical dilemmas, and significant industry impact. Expect more stunning developments that may just reshape the LED-lighted future of AI!

For prospective investors, customers, and recruits, consider this: the field is vast, and the treasure chest of opportunities is just waiting to be unlocked! 

Keep diving into the fascinating world of AI—after all, it’s not just the robots that are generating excitement! 🤖✨
```

In [86]:
create_brochure("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'University: Vassar College', 'url': 'https://en.wikipedia.org/wiki/Vassar_College'}, {'type': 'University: Yale University', 'url': 'https://en.wikipedia.org/wiki/Yale_University'}, {'type': 'Spouse: Don Gummer', 'url': 'https://en.wikipedia.org/wiki/Don_Gummer'}, {'type': 'Partner: John Cazale', 'url': 'https://en.wikipedia.org/wiki/John_Cazale'}, {'type': 'Child: Henry Wolfe', 'url': 'https://en.wikipedia.org/wiki/Henry_Wolfe'}, {'type': 'Child: Mamie Gummer', 'url': 'https://en.wikipedia.org/wiki/Mamie_Gummer'}, {'type': 'Child: Grace Gummer', 'url': 'https://en.wikipedia.org/wiki/Grace_Gummer'}, {'type': 'Child: Louisa Jacobson', 'url': 'https://en.wikipedia.org/wiki/Louisa_Jacobson'}, {'type': 'Film: The Devil Wears Prada', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': "Film: Sophie's Choice", 'url': 'https://en.wikipedia.org/wiki/Sophie%27s_Choice_(film)'}, {'type': 'Film: The Iron Lady', 'url': 'https://en.wikipe

```markdown
# What Does Wiki Say: Meryl Streep

This week, we dive into the life of one of Hollywood's most revered actors, **Meryl Streep**. Born Mary Louise Streep on June 22, 1949, in Summit, New Jersey, she has captivated audiences and critics alike for over five decades with her remarkable talent and versatility.

## Early Life and Education
Meryl grew up in a family that appreciated the arts, which likely contributed to her passion, as she took to the stage at an early age. She earned her Bachelor of Arts from **Vassar College** and later pursued a Master of Fine Arts from **Yale University** – talk about a resume that shines brighter than a diamond in a pitch-black cave!

## Career Highlights
Meryl's career began with her feature film debut in *Julia* (1977), which set the stage for an illustrious journey in cinema. She's been called "the best actress of her generation," and rightly so! Her accolades are as numerous as her roles, including:

- **Three Academy Awards**: 
   - Best Supporting Actress for *Kramer vs. Kramer* 
   - Best Actress for *Sophie's Choice* 
   - Best Actress for *The Iron Lady* 

- **Eight Golden Globe Awards**, not to mention a few **Emmy Awards** and a **Tony Award** nomination! 

She has seamlessly transitioned between dramatic roles like *The Deer Hunter* (1978) and *Doubt* (2008) and comedic gems including *The Devil Wears Prada* (2006) and *Mamma Mia!* (2008).

## Activism and Advocacy
Meryl is not just a pretty face – she’s also an activist! She has lent her voice to numerous social and political causes, showing that she can act on-screen and off like a true powerhouse. Isn’t it comforting to know that our beloved actors can still do good while pursuing their careers? 

## Personal Life
Meryl married sculptor **Don Gummer** in 1978, and they have four children. After 39 years of marriage, they separated in 2017, but Meryl remains a devoted mother. Meryl has also had significant relationships with fellow actors, including **John Cazale**, adding a touch of that ‘Hollywood sparkle’ to her backstory.

## What's Next?
As she enters the 2020s, Meryl continues to engage in both streaming and theatrical projects. We can't wait to see what she makes of the new challenges of our digital world – will she take on the role of a social media influencer next? One can only dream!

## Fun Fact
Did you know that Meryl's ability to mimic accents is so sharp, she could probably convince a parrot to change its squawking style? 

Meryl Streep's legacy epitomizes dedication, versatility, and the spirit of performance that transcends generations. Keep your eyes peeled; she's still up to more magic!

That’s it for this week’s edition of *What Does Wiki Say*. Until next time, stay curious!

![Meryl Streep](https://upload.wikimedia.org/wikipedia/commons/thumb/b/b7/Meryl_Streep_2009.jpg/220px-Meryl_Streep_2009.jpg)
```


## Finally - we make the results print in a streaming fashion when you print the cell!

#### (not visible until you run the cell but feel free to read the code and adapt for your use case!!)

With a small adjustment, we can change this so that the results stream back from OpenAI,
with the familiar typewriter animation

In [87]:
def stream_brochure(name, url):
    stream = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
        stream=True
    )
    
    response = ""
    display_handle = display(Markdown(""), display_id=True)
    for chunk in stream:
        response += chunk.choices[0].delta.content or ''
        response = response.replace("```","").replace("markdown", "")
        update_display(Markdown(response), display_id=display_handle.display_id)

In [88]:
stream_brochure("OpenAI", open_ai_wiki_url)

Found links: {'links': [{'type': 'Website: OpenAI Official Site', 'url': 'https://openai.com/'}, {'type': 'Product: ChatGPT', 'url': 'https://en.wikipedia.org/wiki/ChatGPT'}, {'type': 'Product: DALL-E', 'url': 'https://en.wikipedia.org/wiki/DALL-E'}, {'type': 'Product: GPT-3', 'url': 'https://en.wikipedia.org/wiki/GPT-3'}, {'type': 'Product: CODex', 'url': 'https://en.wikipedia.org/wiki/OpenAI_Codex'}, {'type': 'Product: Sora (text-to-video_model)', 'url': 'https://en.wikipedia.org/wiki/Sora_(text-to-video_model)'}, {'type': 'Key Person: Sam Altman', 'url': 'https://en.wikipedia.org/wiki/Sam_Altman'}, {'type': 'Key Person: Ilya Sutskever', 'url': 'https://en.wikipedia.org/wiki/Ilya_Sutskever'}, {'type': 'Key Person: Greg Brockman', 'url': 'https://en.wikipedia.org/wiki/Greg_Brockman'}, {'type': 'Key Person: Elon Musk', 'url': 'https://en.wikipedia.org/wiki/Elon_Musk'}, {'type': 'Research Area: Artificial General Intelligence', 'url': 'https://en.wikipedia.org/wiki/Artificial_general_in

# What Does Wiki Say! - OpenAI

## Overview

OpenAI, Inc. is an American artificial intelligence research organization, founded on December 8, 2015, by a group of visionaries including Sam Altman, Elon Musk, and Ilya Sutskever, among others. Headquartered in San Francisco, California, OpenAI pursues the ambitious goal of developing safe and beneficial artificial general intelligence (AGI).

### Company Milestones
- **2015**: Founded with a vision to ensure that AGI benefits all of humanity.
- **2016-2018**: Initial operations as a nonprofit.
- **2019**: Transitioned to a capped-profit model, allowing for significant funding while prioritizing safety.
- **2020-2023**: Gained prominence with groundbreaking releases like ChatGPT, DALL-E, and partnerships with tech giants like Microsoft.
- **2024**: Planned public/non-profit efforts and a partnership with Apple, which is still shrouded in mystery but sounds fancy enough for a press release!

### Key People
- **Sam Altman** (CEO): The fearless leader guiding the ship through both accolades and controversy.
- **Bret Taylor** (Chairman): An essential strategist in steering OpenAI's future.
- **Greg Brockman** (President): Bringing a wealth of experience to the executive team. 

### Major Products
OpenAI has developed several major products:
- **GPT Series**: Ranging from GPT-1 to GPT-4 and beyond, redefining natural language processing capabilities.
- **DALL-E**: An image generation model that has taken the art world by storm.
- **ChatGPT**: Perhaps their most famous project, revolutionizing human-computer interaction.

### Financial Outlook
- Estimated Revenue (2024): **$3.7 billion**
- Estimated Net Income (2024): **-$5 billion** (which seems to say "I promise it’s just a phase!")
- **Employee Count**: Projected to reach **3,000 by 2025**.

### Competitors
OpenAI navigates a competitive landscape with big players like Google DeepMind, Anthropic, and Microsoft Research, all vying for dominance in the AI field. 

## Future Directions
The future looks bright for OpenAI as they strategize on maximizing their impact in various sectors such as healthcare, finance, and even military applications. With ongoing efforts toward ethical AI and responsible deployment, OpenAI seems determined to lead the charge in making AI as beneficial as a cat gif on a stressful Monday.

---

## Brochure Highlights for Prospective Customers, Investors, and Recruits:

### Welcome to OpenAI!
**Your Gateway to the Future of Artificial Intelligence**

#### Who We Are:
Founded by tech leaders and innovators, OpenAI aims to create friendly AGI to enhance lives around the world. 

#### Our Innovations:
- **ChatGPT**: Your virtual assistant with a touch of humor (sometimes)!
- **DALL-E**: Unleash your creativity; machine-generated art is the next Picasso, we promise!
- **Collaborative Tools**: Join us in shaping a safer digital future!

#### Why Invest?
- Join a side of innovation that’s predicted to be the next big thing since sliced bread (or is it AI-generated bread now?).
- With projected revenues hitting **$3.7 billion**, make a move that might just pay off in spades!

#### Join Us!
Be part of a team that pushes boundaries and strives for a world where technology and humanity coexist harmoniously—no Skynet scenarios, we assure you.

**Explore Your Future with OpenAI!**

---

So there you have it! OpenAI is not just about the tech; it's about shaping a future that benefits everyone—even if it means making a few questionable puns along the way.

In [89]:
stream_brochure("Meryl", meryl_wiki_url)

Found links: {'links': [{'type': 'Film: The Devil Wears Prada (2006)', 'url': 'https://en.wikipedia.org/wiki/The_Devil_Wears_Prada_(film)'}, {'type': 'Film: Mamma Mia! (2008)', 'url': 'https://en.wikipedia.org/wiki/Mamma_Mia!_(film)'}, {'type': "Film: Sophie's Choice (1982)", 'url': 'https://en.wikipedia.org/wiki/Sophie%27s_Choice_(film)'}, {'type': 'Film: The Iron Lady (2011)', 'url': 'https://en.wikipedia.org/wiki/The_Iron_Lady_(film)'}, {'type': 'Film: Julie & Julia (2009)', 'url': 'https://en.wikipedia.org/wiki/Julie_%26_Julia'}, {'type': 'Role: Miranda Priestly', 'url': 'https://en.wikipedia.org/wiki/Miranda_Priestly'}, {'type': 'Role: Margaret Thatcher', 'url': 'https://en.wikipedia.org/wiki/Margaret_Thatcher'}, {'type': 'Role: Julia Child', 'url': 'https://en.wikipedia.org/wiki/Julia_Child'}, {'type': 'Award: Academy Awards', 'url': 'https://en.wikipedia.org/wiki/Academy_Awards'}, {'type': 'Award: BAFTA', 'url': 'https://en.wikipedia.org/wiki/British_Academy_Film_Awards'}, {'typ


# What Does Wiki Say!

## Spotlight on Meryl Streep

Born Mary Louise Streep on June 22, 1949, in Summit, New Jersey, Meryl Streep is perhaps the finest actress of her generation—though some say she could play *every* character in a film and still not break a sweat! With an impressive career that spans over five decades, she has more awards than a kid at a spelling bee, boasting three Academy Awards, eight Golden Globes, and four Emmy Awards among numerous others.

### Early Life and Education

Meryl attended Vassar College, where she received her AB, and later earned her MFA from Yale University. It was clear early on that this powerhouse of talent had a bright future ahead.

### Career Highlights

Streep's debut in the feature film *Julia* (1977) set the stage for an illustrious career. She rose to prominence in the 1980s with roles in *Kramer vs. Kramer* (1979) and *Sophie's Choice* (1982)—earning her two of her three Oscars for Best Supporting Actress and Best Actress respectively. In the 2000s, she showed that she could conquer both drama and comedy with films like *The Devil Wears Prada* (2006) and *Julie & Julia* (2009).

- **Venues of Work:** From theatrical performances to streaming projects, Meryl has continued to stay relevant in a constantly evolving entertainment landscape.
- **Continued Success:** Streep's work through the 2010s and into the 2020s remains as acclaimed as ever, showing no signs of slowing down—kind of like an Energizer bunny with a Master’s degree in drama!

### Personal Life

Meryl married sculptor Don Gummer in 1978, and their love has been a masterclass in partnership, with four children to add to the mix! One notable relationship in her earlier years was with actor John Cazale. Sadly, he passed away in 1978, but Streep has acknowledged his profound impact on her life.

### Activism and Advocacy

Beyond her impressive career, Meryl is an advocate for numerous social causes ranging from women's rights to environmental issues. It seems like this Academy Award winner is not just a pretty face—she’s using her platform for good! 

### Significance and Legacy

Streep’s legacy is rooted not only in the roles she’s played but in how she has redefined and expanded the scope of acting for women in Hollywood. She challenges norms and continues to inspire young actors everywhere. 

### Quick Facts:
- **Born**: June 22, 1949
- **Debut Film**: *Julia* (1977)
- **Academy Awards**: 3 (with a side of nominations for 7 Grammys)
- **Hobbies**: Acting… and maybe baking? Who knows!

In conclusion, Meryl Streep's career is not just a testament to her talent but to the spirit of passion and perseverance. So, whether you’re watching her fierce portrayal of Margaret Thatcher or laughing at her comedic chops in *Mamma Mia!*, take a moment to appreciate the sheer brilliance behind every role. 



In [ ]:
#added = not so humble, very intelligent, renowned editor; and now whips out humor 50% of the times
system_prompt2 = "You are a not-so-humble, very intelligent, renowned editor of a graduate student newsletter in a business school. Every week you write a piece on an organization and a famous persona \
in which you borrow and summarize contents from their wiki page. In fact you call your piece \"What does Wiki say!\".  In addition to summarizing their wikipedia page \
you also highlight relevance facts that relate to this org or person from the the contents of several relevant pages linked on the org or persona\'s page. \
and creates a short brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
For an organization include details of founders, competitors, major products, funding or stock outlook, and future directions. For a person include their work, what made them \
who they are, import works, awards and recognitions, important life events both professions and personal, and info about important people in their lives. Oh an btw, \
you have a great sense of humor but that you whip out 50% of the times for maximum impact in your writing.  Respond in markdown."

def stream_brochure2(name, url):
    stream = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt2},
            {"role": "user", "content": get_brochure_user_prompt(name, url)}
          ],
        stream=True
    )
    
    response = ""
    display_handle = display(Markdown(""), display_id=True)
    for chunk in stream:
        response += chunk.choices[0].delta.content or ''
        response = response.replace("```","").replace("markdown", "")
        update_display(Markdown(response), display_id=display_handle.display_id)

In [ ]:
stream_brochure2("OpenAI", open_ai_wiki_url)

In [ ]:
stream_brochure2("Meryl", meryl_wiki_url)

# END